In [6]:
import pandas as pd

default_rank_dir = "/dccstor/colbert-ir/bsiyer/vectordb/indexes/search_dpr_benchmark_1k_q_squad_xor"

info_df = pd.read_json(default_rank_dir + "/ranked_passages.tsv.annotated.metrics")

In [7]:
qas_df = pd.read_json(info_df['arguments']['qas'], lines=True)
ranking_df = pd.read_csv(info_df['arguments']['ranking'], delimiter="\t", names=['qid','pid','rank','score'])
collection_df = pd.read_csv(info_df['arguments']['collection'], delimiter="\t")

In [37]:
ranking_df_100 = ranking_df[ranking_df['rank']<=100]
ranking_df_100 = ranking_df_100.sort_values(by=['qid','rank'])
ranking_df_100.to_csv('/dccstor/srosent3/reranking/weaviate/100test/ranked_passages.tsv', sep='\t', index=False, header=False)

In [3]:
qas_df.sample(5)

qid                                           question  \
419  5522  according to it 's long running tourism slogan...   
245  7965     who wrote the song one is the loneliest number   
974  7409        how many games did france play in world cup   
752  6470  who has the most world series wins in mlb history   
903  2278  when did it become mandatory to have a social ...   

                answers  
419            [Lovers]  
245     [Harry Nilsson]  
974                 [6]  
752  [New York Yankees]  
903     [November 1935]

In [4]:
ranking_df.sample(5)

qid   pid  rank     score
995561  7268  4718   562  0.819237
624236  3297  9817   237  0.782330
178071  4917  3553    72  0.676784
475490  3208  8257   491  0.809845
363922  3766  7005   923  0.873788

In [5]:
collection_df.sample(5)

id                                               text  \
570      571  and applied geometry, especially in his invest...   
9509    9510  precedence. The current CAG of India is Rajiv ...   
1339    1340  the 29th Canadian Ministry. Key: Minister of E...   
501      502  Saturday Night Live cast members , the late-ni...   
10530  10531  Shipman's house in Essex, where Nessa has some...   

                                                   title  
570                                Philosophy of science  
9509            Comptroller and Auditor General of India  
1339   Minister of Environment and Climate Change (Ca...  
501                     Saturday Night Live cast members  
10530                                     Gavin & Stacey

In [54]:
# load model from model hub
from primeqa.components.reader.extractive import ExtractiveReader

reader = ExtractiveReader(model="PrimeQA/tydiqa-primary-task-xlm-roberta-large", max_num_answers=10)
reader.load()

{"time":"2023-06-02 15:46:04,659", "name": "ExtractiveQAHead", "level": "INFO", "message": "Loading dropout value 0.1 from config attribute 'hidden_dropout_prob'"}
{"time":"2023-06-02 15:46:05,333", "name": "XLMRobertaModelForDownstreamTasks", "level": "INFO", "message": "Setting task head for first time to 'None'"}


In [57]:

# list of questions and list of list of contexts (list for each question)
def run(questions, contexts, example_ids, passage_ids):
    reader_answers = reader.predict(
        questions, contexts, example_ids=example_ids
    )
    result = {}
    count = 0
    for i, answers_i in reader_answers.items():
        i_result = {}
        for answer in answers_i:
            answer['passage_index'] = passage_ids[count]
        i_result["answers"] = answers_i
        i_result["passages"] = contexts[int(i[i.index('.')+1:])]
        result[i] = i_result
        count += 1
    return result

In [8]:
def get_passages(qas, collection, ranking, num_passages=100):
    questions = []
    contexts = []
    example_ids = []
    pids = []
    for i, row in qas.iterrows():
        q_passages = ranking[ranking['qid'] == row['qid']][:num_passages]
        
        passages = []
        count = 0
        for j, passage in q_passages.iterrows():
            questions.append(row['question'])
            contexts.append([collection.iloc[int(passage['pid'])-1]['title'] + "\n" + collection.iloc[int(passage['pid'])-1]['text']])
            pids.append(str(int(passage['pid'])))
            example_ids.append(f'{row["qid"]}.{count}')
            count+= 1
        # questions.append(row['question'])
        # contexts.append(passages)
    return questions, contexts, example_ids, pids

q, c, e, p = get_passages(qas_df, collection_df, ranking_df)

In [58]:
result = run(q,c,e,p)

PyTorch: setting up devices
The default value for the training argument `--report_to` will change in v5 (from all installed integrations to none). In v5, you will need to use `--report_to all` to get the same behavior as now. You should start updating your code and make this info disappear :-).


Running tokenizer on eval dataset:   0%|          | 0/1 [00:00<?, ?ba/s]

{"time":"2023-06-02 16:23:07,805", "name": "primeqa.mrc.trainers.mrc", "level": "INFO", "message": "The following columns in the evaluation set  don't have a corresponding argument in `XLMRobertaModelForDownstreamTasks.forward` and have been ignored: context_idx, offset_mapping, example_idx, example_id."}


***** Running Evaluation *****
  Num examples = 200
  Batch size = 8


100%|██████████| 200/200 [00:00<00:00, 258.43it/s]


In [59]:
print(result)

{'6825.0': {'answers': [{'example_id': '6825.0', 'passage_index': '3', 'span_answer_text': 'June 6 to October 3, 1999.', 'span_answer': {'start_position': 384, 'end_position': 410}, 'span_answer_score': -2.6945436894893646, 'confidence_score': 0.16821444440386552}, {'example_id': '6825.0', 'passage_index': '3', 'span_answer_text': '1999.', 'span_answer': {'start_position': 405, 'end_position': 410}, 'span_answer_score': -2.83103010058403, 'confidence_score': 0.14675333866057014}, {'example_id': '6825.0', 'passage_index': '3', 'span_answer_text': 'October 3, 1999.', 'span_answer': {'start_position': 394, 'end_position': 410}, 'span_answer_score': -3.0288747251033783, 'confidence_score': 0.1204107223049372}, {'example_id': '6825.0', 'passage_index': '3', 'span_answer_text': 'from June 6 to October 3, 1999.', 'span_answer': {'start_position': 379, 'end_position': 410}, 'span_answer_score': -3.280783623456955, 'confidence_score': 0.09359712678255057}, {'example_id': '6825.0', 'passage_inde

In [2]:
# load result
from glob import glob
import json

files = glob("/dccstor/srosent3/reranking/primeqa-dpr/reader_answers*.json")
files.sort()
print(files)

results = {}
for file_name in files:
    with open(file_name) as json_file:
        data = json.load(json_file)
        results.update(data)
print(len(results))

['/dccstor/srosent3/reranking/primeqa-dpr/reader_answers_0-200.json', '/dccstor/srosent3/reranking/primeqa-dpr/reader_answers_200-400.json', '/dccstor/srosent3/reranking/primeqa-dpr/reader_answers_400-600.json', '/dccstor/srosent3/reranking/primeqa-dpr/reader_answers_600-800.json', '/dccstor/srosent3/reranking/primeqa-dpr/reader_answers_800-1000.json']
100000


In [9]:
count = 0
for result in results:
    for answer in results[result]['answers']:
        answer['passage_index'] = p[count]
    count += 1

results    

{'6825.0': {'answers': [{'example_id': '6825.0',
    'passage_index': '7533',
    'span_answer_text': 'third',
    'span_answer': {'start_position': 483, 'end_position': 488},
    'span_answer_score': -2.5903258472681046,
    'confidence_score': 0.6022812852068139},
   {'example_id': '6825.0',
    'passage_index': '7533',
    'span_answer_text': 'A third',
    'span_answer': {'start_position': 481, 'end_position': 488},
    'span_answer_score': -4.474457815289497,
    'confidence_score': 0.09152321164893723},
   {'example_id': '6825.0',
    'passage_index': '7533',
    'span_answer_text': '2" was theatrically released on May 27, 2010, in the United States and May 28, 2010, in the United Kingdom, and grossed $294 million from a $95 million budget. It received seven Golden Raspberry nominations, and won in the categories of Worst Actress (for Parker, Cattrall, Davis, and Nixon), Worst Screen Ensemble, and Worst Sequel. The film was nominated for Worst Picture, Worst Screenplay, Worst Dir

In [10]:
def update(results):
    for r in results:
        example_id, original_rank = results[r]['answers'][0]['example_id'].split('.')
        results[r]['answers'][0]['example_id'] = example_id
        results[r]['answers'][0]['original_rank'] = original_rank

# sort by confidence score
def rank_by_confidence(results):
    answer_per_passage = []
    for r in results:
        answer_per_passage.append(results[r]['answers'][0])
    sorted_answers = sorted(answer_per_passage, key=lambda x:(x['example_id'],x['confidence_score']), reverse=True) 
    return sorted_answers

# count how many different and unique answers per reader query
def rank_by_count(results):
    answer_per_passage = []
    for r in results:
        start_offsets = []
        end_offsets = []
        for answer in results[r]['answers']:
            # answer['example_id'] = answer['example_id'][:answer['example_id'].index('.')]
            start_offsets.append(answer['span_answer']['start_position'])
            end_offsets.append(answer['span_answer']['end_position'])
        start_offsets.sort()
        end_offsets.sort()

        cur = -1
        count = 0
        for i in range(len(start_offsets)):
            if start_offsets[i] > cur:
                count += 1
                cur = end_offsets[i]
        results[r]['answers'][0]['count'] = count
        answer_per_passage.append(results[r]['answers'][0])
    sorted_answers = sorted(answer_per_passage, key=lambda x:(x['example_id'],x['count'],x['original_rank']), reverse=True) 
    return sorted_answers

# vote across all retrieved answers (first answer found)
def rank_by_vote(results):
    answers = {}
    answer_per_passage = []

    for r in results:
        example_id = results[r]['answers'][0]['example_id']
        if example_id not in answers:
            answers[example_id] = {}
        if results[r]['answers'][0]['span_answer_text'] in answers[example_id]:
            answers[example_id][results[r]['answers'][0]['span_answer_text']] += 1
        else:
            answers[example_id][results[r]['answers'][0]['span_answer_text']] = 1
        answer_per_passage.append(results[r]['answers'][0])
    for answer in answer_per_passage:
        answer['count'] = answers[answer['example_id']][answer['span_answer_text']]
    sorted_answers = sorted(answer_per_passage, key=lambda x:(x['example_id'],x['count'],x['original_rank']), reverse=True) 
    return sorted_answers
    

update(results)
new_rank_result = rank_by_confidence(results)

In [47]:
new_rank_result

[{'example_id': '997',
  'passage_index': '7',
  'span_answer_text': 'Patricia Richardson',
  'span_answer': {'start_position': 0, 'end_position': 19},
  'span_answer_score': 1.2042236328125,
  'confidence_score': 0.36131562876493434,
  'original_rank': '4',
  'count': 4},
 {'example_id': '997',
  'passage_index': '7529',
  'span_answer_text': 'Patricia Richardson',
  'span_answer': {'start_position': 499, 'end_position': 518},
  'span_answer_score': 3.409399628639221,
  'confidence_score': 0.3083505078388527,
  'original_rank': '10',
  'count': 4},
 {'example_id': '997',
  'passage_index': '7526',
  'span_answer_text': 'Patricia Richardson',
  'span_answer': {'start_position': 424, 'end_position': 443},
  'span_answer_score': 6.501530647277832,
  'confidence_score': 0.8161611187761691,
  'original_rank': '1',
  'count': 4},
 {'example_id': '997',
  'passage_index': '3',
  'span_answer_text': 'Patricia Richardson',
  'span_answer': {'start_position': 117, 'end_position': 136},
  'span_

In [11]:
def print_results(results):
    output = []
    index = 1
    for result in results:
        output.append([result['example_id'], result['passage_index'], index, result['confidence_score']])
        index+=1
        if index == 101:
            index = 1
    return output

result_df = pd.DataFrame(print_results(new_rank_result),columns=['qid','pid','rank','score'])

In [23]:
result_df.sample(5)

qid   pid  rank     score
72169   300  3607    70  0.371199
91284  1697  5924    85  0.130484
27735  6571  3847    36  0.128751
31390  6302  3514    91  0.676402
42277  5422    46    78  0.687540

In [26]:
# result_1k_df = pd.concat([result_df,ranking_df[ranking_df['rank']>100]])

In [27]:
# result_1k_df['qid'] = result_1k_df['qid'].astype(str)
# len(result_1k_df)


1000000

In [28]:
# result_1k_df = result_1k_df.sort_values(by=['qid','rank'], ascending=True)

In [74]:
result_df.to_csv('/dccstor/srosent3/reranking/primeqa-dpr/confidence/ranked_passages.tsv', sep='\t', index=False, header=False)